In [1]:
import pandas as pd
import numpy as np
xls = pd.ExcelFile('/home/techverx/Downloads/Data (1).xlsx')
df2 = pd.read_excel(xls, 'Final Data', header=1)
df2=df2.drop('Unnamed: 0',axis=1)
df2=df2.drop('Status',axis=1)
df2=df2.drop(['Year','Month'],axis=1)
df3=df2[(df2['On Hand Qty']>0) & (df2['Location Name']== "Main Warehouse")].reset_index(drop=True)
df2=df2[df2['ProductID'].isin(df3["ProductID"].unique())]
df2=df2[df2['On Hand Qty'] > 0]
df2=df2[df2['Location Name']!='Main Warehouse']
df2['Date']=pd.to_datetime(df2['Date'], infer_datetime_format=True).dt.date
table1 = pd.DataFrame(df2.pivot_table(values = ['Sales (Qty)','IN QTY','OUT QTY'],\
                                      index = ['ProductID'],\
                                      aggfunc={'Sales (Qty)':np.sum,'IN QTY':np.sum,'OUT QTY':np.sum}))
table1 = table1.reindex(table1['Sales (Qty)'].sort_values(ascending=False).index)
table1.reset_index(inplace=True)
table2 = pd.DataFrame(df2.pivot_table(values = ['Sales (Qty)','IN QTY','OUT QTY'],\
                                      index = ['ProductID','ColorName'],\
                                      aggfunc={'Sales (Qty)':np.sum,'IN QTY':np.sum,'OUT QTY':np.sum}))
table2 = table2.reindex(table2['Sales (Qty)'].sort_values(ascending=False).index)
table2.reset_index(inplace=True)
table3 = pd.DataFrame(df2.pivot_table(values = ['Sales (Qty)','IN QTY','OUT QTY'],\
                                      index = ['ProductID','ColorName','SizeID'],\
                                       aggfunc={'Sales (Qty)':np.sum,'IN QTY':np.sum,'OUT QTY':np.sum}))
table3 = table3.reindex(table3['Sales (Qty)'].sort_values(ascending=False).index)
table3.reset_index(inplace=True)
table4 = pd.DataFrame(df2.pivot_table(values = ['Sales (Qty)','IN QTY','OUT QTY'],\
                                      index = ['ProductID','ColorName','SizeID','Location Name'],\
                                       aggfunc={'Sales (Qty)':np.sum,'IN QTY':np.sum,'OUT QTY':np.sum}))
table4 = table4.reindex(table4['Sales (Qty)'].sort_values(ascending=False).index)
table4.reset_index(inplace=True)
merged1 = pd.merge(table1,table2,'left', on=['ProductID'])

merged1=merged1.rename(columns={merged1.columns[1]:'a', merged1.columns[2]: 'b',merged1.columns[3]:'c',merged1.columns[5]:'IN qty',merged1.columns[6]:'Out qty',merged1.columns[7]:'sals qty'})
merged2 = pd.merge(merged1,table3,'left', on=['ProductID','ColorName'])
merged3 = pd.merge(merged2,table4,'left', on=['ProductID','ColorName','SizeID'])
data=merged3.drop(['a','b','c','IN qty','Out qty','sals qty','IN QTY_x','OUT QTY_x','Sales (Qty)_x'],axis=1)
data=data.rename(columns={'Sales (Qty)_y':'Sales (Qty)','OUT QTY_y':'OUT QTY','IN QTY_y':'IN QTY'})
data['Sales forecast']=""
data['Min Qty']=""


In [2]:
data.set_index(['ProductID','ColorName','SizeID','Location Name'],inplace=True)

In [3]:
df2['Date']=pd.to_datetime(df2['Date'], infer_datetime_format=True).dt.date
dal=df2['Date'].unique().tolist()
start_date=dal[0]
df1st_date = df2[df2['Date'] ==start_date]
df1st_date.reset_index(drop=True,inplace=True)
df1st_date.set_index(['ProductID','ColorName','SizeID','Location Name'],inplace=True)

In [4]:
df2['Date']=pd.to_datetime(df2['Date'], infer_datetime_format=True).dt.date
dal=df2['Date'].unique().tolist()
end_date=dal[-1]
end_date = df2[df2['Date'] ==end_date]
end_date.reset_index(drop=True,inplace=True)
end_date.set_index(['ProductID','ColorName','SizeID','Location Name'],inplace=True)

In [5]:
data['Opening QTY']=df1st_date['Opening QTY']
data['On Hand Qty']=end_date['On Hand Qty']
data['Transit Qty']=end_date['On Hand Qty']
data['Total Qty']=data['Transit Qty']/data['On Hand Qty']
data['Effective Days']=df2[df2['On Hand Qty']>0].groupby(['ProductID','ColorName','SizeID','Location Name'],sort=False)['On Hand Qty'].count()
data['Replanish Days']=np.random.randint(1, 6, data.shape[0])
data['Sales Per Day']=data['Sales (Qty)']//data['Effective Days']
data['Growth Factor']=0
data['Shop Priority']=1 



In [6]:
data.reset_index(inplace=True)


In [7]:
pro=data['ProductID'].unique().tolist()
siz=data['SizeID'].unique().tolist()
col=data['ColorName'].unique().tolist()


In [8]:
p_count=[]
product_add=[]
products=[]

for i in range(len(pro)):
    data1=data[data['ProductID']==pro[i]]
    
    
    
   
    
    new1=pd.pivot_table(data1,
        index = ['ProductID'],
           values = ['IN QTY','OUT QTY','Sales (Qty)','Opening QTY','On Hand Qty','Transit Qty','Total Qty'],
           fill_value = '',
           aggfunc = np.sum,
           margins = True,
           margins_name = f"{pro[i]} Total"
                            )
    products.append(new1)
    b=new1.iloc[1]
    data2 = data1.append(b)
    data2['ProductID'].fillna(method='ffill',limit=1,inplace=True)
    data2['ColorName'].fillna(method='ffill',limit=1,inplace=True)
    data2['SizeID'].fillna(method='ffill',limit=1,inplace=True)
    data2['Location Name'].fillna('Total',inplace=True)
    o=data2['ProductID'].count()
    p_count.append(o)
    
    product_add.append(data2)


In [9]:
Product_sum=pd.concat(product_add,ignore_index=True)



In [10]:
dic_color_product={}
for i in range(len(pro)):
    d=data[(data['ProductID']==pro[i])& data['ColorName']]
    c=d['ColorName'].unique().tolist()
    dix={pro[i]:c}
    dic_color_product.update(dix)
    

In [11]:
color_sum=[]
colorcount=[]
colort=[]

for i,v in dic_color_product.items():
   
    
    for k in range(len(v)):
        data1=data[(data['ProductID']==i)&( data['ColorName']==v[k])]

        new2=pd.pivot_table(data1,
            index = ['ProductID','ColorName'],
            values = ['IN QTY','OUT QTY','Sales (Qty)','Opening QTY','On Hand Qty','Transit Qty','Total Qty'],
               
            aggfunc = np.sum,
            margins = True,
            margins_name = f"{v[k]} Total"
                                )
        colort.append(new2)
    
        b=new2.iloc[1]
        
        data2 = data1.append(b, ignore_index = False)
        data2['ProductID'].fillna(method='ffill',limit=1,inplace=True)
        data2['ColorName'].fillna(method='ffill',limit=1,inplace=True)
        data2['SizeID'].fillna(method='ffill',limit=1,inplace=True)
        data2['Location Name'].fillna('Total',inplace=True)
        w=data2['ColorName'].count()
        colorcount.append(w)
        
        color_sum.append(data2)


In [12]:
color_total_sum=pd.concat(color_sum,ignore_index=True)

In [13]:
diction_color_product={}
for i in range(len(pro)):
    d=Product_sum[(Product_sum['ProductID']==pro[i])& Product_sum['ColorName']]
    c=d['ColorName'].unique().tolist()
    dix={pro[i]:c}
    diction_color_product.update(dix)
color_count_after=[]
for i,v in dic_color_product.items():
    
    for k in range(len(v)):
        data1=Product_sum[(Product_sum['ProductID']==i)&( Product_sum['ColorName']==v[k])]

        t=data1['ColorName'].count()
        color_count_after.append(t)
   

In [14]:
combining_color_product=[]
val=0
for index, (value1, value2,) in enumerate(zip(color_count_after, colort)):
    
        

   
    val=value1 + val
        
        
    
    c=Product_sum[:val].append(value2.iloc[1])
    c['ProductID'].fillna(method='ffill',limit=1,inplace=True)
    c['ColorName'].fillna(method='ffill',limit=1,inplace=True)
    c['SizeID'].fillna(method='ffill',limit=1,inplace=True)
    c['Location Name'].fillna('Total',inplace=True)
    
    
    
    combining_color_product.append(c)

In [15]:
final_both=pd.concat(combining_color_product,ignore_index=True).drop_duplicates()


In [16]:

qw=[]
ji=[]
for i,v in dic_color_product.items():
  
    
    for k in range(len(v)):
        for j in siz:
            data1=data[(data['ProductID']==i)&( data['ColorName']==v[k])&(data['SizeID']==j)]
            if data1.empty:
                pass
            else:
                new1=pd.pivot_table(data1,
                index = ['ProductID','ColorName','SizeID'],
                values = ['IN QTY','OUT QTY','Sales (Qty)','Opening QTY','On Hand Qty','Transit Qty','Total Qty'],
                fill_value = '',
               aggfunc = np.sum,
               margins = True,
               margins_name = "Total"
                            )
                
                b=new1.iloc[1]
                data2 = data1.append(b)
                data2['ProductID'].fillna(method='ffill',limit=1,inplace=True)
                data2['ColorName'].fillna(method='ffill',limit=1,inplace=True)
                data2['SizeID'].fillna(method='ffill',limit=1,inplace=True)
                data2['Location Name'].fillna('Total',inplace=True)
                o=data2['ProductID'].count()
                qw.append(data2)
                

                product_add.append(data2)
                ji.append(o)

    

In [17]:
size_sum=pd.concat(qw,ignore_index=True)


In [18]:
sizeadd=[]

for i,v in dic_color_product.items():
  
    
    for k in range(len(v)):
        for j in siz:
            data1=size_sum[(size_sum['ProductID']==i)&( size_sum['ColorName']==v[k])&(size_sum['SizeID']==j)]
            if data1.empty:
                pass
            else:
                re=data1['SizeID'].count()
                
                
                
                sizeadd.append(re)
                

In [19]:
iction_color_product={}
for i in range(len(pro)):
    d=size_sum[(size_sum['ProductID']==pro[i])& size_sum['ColorName']]
    c=d['ColorName'].unique().tolist()
    dix={pro[i]:c}
    iction_color_product.update(dix)
olor_count_after=[]
for i,v in iction_color_product.items():
    
    for k in range(len(v)):
        data1=size_sum[(size_sum['ProductID']==i)&( size_sum['ColorName']==v[k])]
#         print(data1.index[-1])
        t=data1['ColorName'].count()
        olor_count_after.append(t)


In [20]:
ombining_color_product=[]
val=0
for index, (value1, value2,) in enumerate(zip(olor_count_after , colort)):
    val=value1 + val
    c=size_sum[:val].append(value2.iloc[1])
    c['ProductID'].fillna(method='ffill',limit=1,inplace=True)
    c['ColorName'].fillna(method='ffill',limit=1,inplace=True)
    c['Location Name'].fillna('Total',inplace=True)
    ombining_color_product.append(c)


In [21]:
final_before=pd.concat(ombining_color_product,ignore_index=True).drop_duplicates()



In [22]:
product_count=[]
for i in range(len(pro)):
    data1=final_before[final_before['ProductID']==pro[i]]
    z=data1['ProductID'].count()
    product_count.append(z)
   

In [23]:
mbining_color_product=[]
val=0
for index, (value1, value2,) in enumerate(zip(product_count , products)):
    val=value1 + val
    c=final_before[:val].append(value2.iloc[1])
    c['ProductID'].fillna(method='ffill',limit=1,inplace=True)
    c['Location Name'].fillna('Total',inplace=True)
    mbining_color_product.append(c)

In [24]:
final=pd.concat(mbining_color_product,ignore_index=True).drop_duplicates()
final.reset_index(drop=True)


ProductID ColorName  SizeID                  Location Name  IN QTY  \
0     M-KL-0550028     BLACK    10.0  University Road Shop-Peshawar     2.0   
1     M-KL-0550028     BLACK    10.0             G-9 Shop-Islamabad     1.0   
2     M-KL-0550028     BLACK    10.0          Gulgashat Shop-Multan     4.0   
3     M-KL-0550028     BLACK    10.0      King Mall Shop-Gujranwala     0.0   
4     M-KL-0550028     BLACK    10.0             F-7 Shop-Islamabad     0.0   
...            ...       ...     ...                            ...     ...   
5870  M-KL-0400135     BLACK    40.0                          Total     0.0   
5871  M-KL-0400135     BLACK    11.0       Baghban Pura Shop-Lahore     0.0   
5872  M-KL-0400135     BLACK    11.0                          Total     0.0   
5873  M-KL-0400135     BLACK     NaN                          Total     0.0   
5874  M-KL-0400135       NaN     NaN                          Total     0.0   

      OUT QTY  Sales (Qty) Sales forecast Min Qty  Opening QTY  On Hand Qty  \
0         0.0          5.0                                 5.0          2.0   
1         0.0          3.0                                 5.0          3.0   
2         0.0          3.0                                 4.0          5.0   
3         0.0          2.0                                 6.0          4.0   
4         0.0          1.0                                 6.0          5.0   
...       ...          ...            ...     ...          ...          ...   
5870      0.0          0.0            NaN     NaN          2.0          2.0   
5871      0.0          0.0                                 1.0          NaN   
5872      0.0          0.0            NaN     NaN          0.0          0.0   
5873      0.0          1.0            NaN     NaN         38.0         38.0   
5874      0.0          3.0            NaN     NaN         83.0         81.0   

      Transit Qty  Total Qty  Effective Days  Replanish Days  Sales Per Day  \
0             2.0        1.0            16.0             4.0            0.0   
1             3.0        1.0            16.0             2.0            0.0   
2             5.0        1.0            16.0             3.0            0.0   
3             4.0        1.0            16.0             3.0            0.0   
4             5.0        1.0            16.0             4.0            0.0   
...           ...        ...             ...             ...            ...   
5870          2.0        2.0             NaN             NaN            NaN   
5871          NaN        NaN            14.0             1.0            0.0   
5872          0.0        0.0             NaN             NaN            NaN   
5873         38.0       20.0             NaN             NaN            NaN   
5874         81.0       42.0             NaN             NaN            NaN   

      Growth Factor  Shop Priority  
0               0.0            1.0  
1               0.0            1.0  
2               0.0            1.0  
3               0.0            1.0  
4               0.0            1.0  
...             ...            ...  
5870            NaN            NaN  
5871            0.0            1.0  
5872            NaN            NaN  
5873            NaN            NaN  
5874            NaN            NaN  

[5875 rows x 18 columns]

In [25]:
pd.set_option("max_rows", 5000,'max_columns',30)
final.fillna("",inplace=True)

In [26]:
final.head(5000)

ProductID  ColorName SizeID                  Location Name  IN QTY  \
0       M-KL-0550028      BLACK   10.0  University Road Shop-Peshawar     2.0   
1       M-KL-0550028      BLACK   10.0             G-9 Shop-Islamabad     1.0   
2       M-KL-0550028      BLACK   10.0          Gulgashat Shop-Multan     4.0   
3       M-KL-0550028      BLACK   10.0      King Mall Shop-Gujranwala     0.0   
4       M-KL-0550028      BLACK   10.0             F-7 Shop-Islamabad     0.0   
5       M-KL-0550028      BLACK   10.0        GT Road Shop-Gujranwala     2.0   
6       M-KL-0550028      BLACK   10.0       Baghban Pura Shop-Lahore     1.0   
7       M-KL-0550028      BLACK   10.0                          Total    10.0   
8       M-KL-0550028      BLACK    9.0          Gulgashat Shop-Multan     5.0   
9       M-KL-0550028      BLACK    9.0        GT Road Shop-Gujranwala     3.0   
10      M-KL-0550028      BLACK    9.0             G-9 Shop-Islamabad     2.0   
11      M-KL-0550028      BLACK    9.0  University Road Shop-Peshawar     1.0   
12      M-KL-0550028      BLACK    9.0       Baghban Pura Shop-Lahore     0.0   
13      M-KL-0550028      BLACK    9.0             F-7 Shop-Islamabad     1.0   
14      M-KL-0550028      BLACK    9.0      King Mall Shop-Gujranwala     0.0   
15      M-KL-0550028      BLACK    9.0                          Total    12.0   
16      M-KL-0550028      BLACK    7.0             G-9 Shop-Islamabad     1.0   
17      M-KL-0550028      BLACK    7.0          Gulgashat Shop-Multan     2.0   
18      M-KL-0550028      BLACK    7.0  University Road Shop-Peshawar     1.0   
19      M-KL-0550028      BLACK    7.0       Baghban Pura Shop-Lahore     1.0   
20      M-KL-0550028      BLACK    7.0             F-7 Shop-Islamabad     0.0   
21      M-KL-0550028      BLACK    7.0        GT Road Shop-Gujranwala     0.0   
22      M-KL-0550028      BLACK    7.0      King Mall Shop-Gujranwala     0.0   
23      M-KL-0550028      BLACK    7.0                          Total     5.0   
24      M-KL-0550028      BLACK    8.0        GT Road Shop-Gujranwala     2.0   
25      M-KL-0550028      BLACK    8.0  University Road Shop-Peshawar     0.0   
26      M-KL-0550028      BLACK    8.0             F-7 Shop-Islamabad     1.0   
27      M-KL-0550028      BLACK    8.0       Baghban Pura Shop-Lahore     1.0   
28      M-KL-0550028      BLACK    8.0             G-9 Shop-Islamabad     0.0   
29      M-KL-0550028      BLACK    8.0          Gulgashat Shop-Multan     0.0   
30      M-KL-0550028      BLACK    8.0      King Mall Shop-Gujranwala     0.0   
31      M-KL-0550028      BLACK    8.0                          Total     4.0   
32      M-KL-0550028      BLACK                                 Total    31.0   
33      M-KL-0550028      BROWN   10.0        GT Road Shop-Gujranwala     0.0   
34      M-KL-0550028      BROWN   10.0  University Road Shop-Peshawar     0.0   
35      M-KL-0550028      BROWN   10.0      King Mall Shop-Gujranwala     0.0   
36      M-KL-0550028      BROWN   10.0             G-9 Shop-Islamabad     1.0   
37      M-KL-0550028      BROWN   10.0          Gulgashat Shop-Multan     0.0   
38      M-KL-0550028      BROWN   10.0       Baghban Pura Shop-Lahore     0.0   
39      M-KL-0550028      BROWN   10.0             F-7 Shop-Islamabad     1.0   
40      M-KL-0550028      BROWN   10.0                          Total     2.0   
41      M-KL-0550028      BROWN    9.0        GT Road Shop-Gujranwala     1.0   
42      M-KL-0550028      BROWN    9.0             G-9 Shop-Islamabad     2.0   
43      M-KL-0550028      BROWN    9.0             F-7 Shop-Islamabad     2.0   
44      M-KL-0550028      BROWN    9.0          Gulgashat Shop-Multan     1.0   
45      M-KL-0550028      BROWN    9.0       Baghban Pura Shop-Lahore     1.0   
46      M-KL-0550028      BROWN    9.0      King Mall Shop-Gujranwala     1.0   
47      M-KL-0550028      BROWN    9.0  University Road Shop-Peshawar     2.0   
48      M-KL-0550028      BROWN    9.0    